# QASPER evaluation

In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import json
import os
import plotly.express as px
import plotly.graph_objects as go
import dataset_reader
from transformers.tokenization_utils_base import BatchEncoding

/Users/ag2435/anaconda3/envs/arxiv-agent/lib/python3.12/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [3]:
# input_path = 'original_data/qasper-train-dev-v0.3/qasper-train-v0.3.json'
input_path = 'original_data/qasper-test-and-evaluator-v0.3/qasper-test-v0.3.json'
output_path = 'data'
split = 'test'
assert split in input_path

In [4]:
reader = dataset_reader.QasperReader(include_global_attention_mask=False)
instances = list(reader._read(input_path))

In [5]:
reader._stats

defaultdict(int,
            {'number of documents': 416,
             'number of questions': 1451,
             'number of answers': 3554,
             'questions with multiple answers': 1427,
             'extractive questions': 1817,
             'extractive questions with multiple spans': 787,
             'multiple_evidence_spans_count': 1063,
             'freeform answers': 878,
             'answers with table or figure as evidence': 391,
             'answers with no evidence': 444,
             'unanswerable questions': 366,
             'yes/no questions': 493,
             'number of truncated contexts': 2})

In [6]:
# plot histogram of full_text lengths
question_token_lengths = []
for inst in instances:
    question_token_lengths.append(len(inst['question_with_context']))
    
px.histogram(question_token_lengths, 
             title=f'Histogram of question + context token lengths (total={len(question_token_lengths)})')

## Save instances to JSON

In [7]:
# recursively check the type of each field in the dataset
def check_type(data, level=0):
    tabs = '\t' * level
    if isinstance(data, dict):
        for key, value in data.items():
            print(f'{tabs}{key}: {type(value)}')
            check_type(value, level + 1)
    elif isinstance(data, list):
        for i in data:
            check_type(i, level + 1)
    else:
        pass
        # print(f'{tabs}{type(data)}')
        # if isinstance(data, BatchEncoding):
        #     print(f'{tabs}{data[:100]}')

In [8]:
check_type(instances[0])

question_with_context: <class 'list'>
paragraph_indices: <class 'list'>
evidence: <class 'list'>
answer: <class 'list'>
metadata: <class 'dict'>
	question: <class 'str'>
	question_tokens: <class 'list'>
	paragraphs: <class 'list'>
	context_tokens: <class 'list'>
	question_id: <class 'str'>
	article_id: <class 'str'>
	all_answers: <class 'list'>
			text: <class 'str'>
			type: <class 'str'>
			text: <class 'str'>
			type: <class 'str'>
			text: <class 'str'>
			type: <class 'str'>
			text: <class 'str'>
			type: <class 'str'>
			text: <class 'str'>
			type: <class 'str'>
			text: <class 'str'>
			type: <class 'str'>
	all_evidence: <class 'list'>
	all_evidence_masks: <class 'list'>


In [9]:
# save instances to file
with open(os.path.join(output_path, f'{split}_instances.json'), 'w') as f:
    # pretty print json
    json.dump(instances, f, indent=4)